# Data Storytelling

 - Explore the data below (ie features, stats, and visualizations).
 - Develop 2-3 questions/theses that might be addressed by these data.
 - Clean and combine data sources.
 - Choose a model. What aspects of the model will help support your thesis or answer your question?
 - Assess and interpret your model.



In [46]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

[data repository](https://github.com/GettysburgDataScience/datasets/tree/main/us_political)

In [47]:
elec_df = pd.read_csv('https://raw.githubusercontent.com/GettysburgDataScience/datasets/refs/heads/main/us_political/countypres_2000-2024.csv')
health_df = pd.read_csv('https://raw.githubusercontent.com/GettysburgDataScience/datasets/refs/heads/main/us_political/countyHealth_2025.csv', skiprows = [1])
agesex_df = pd.read_csv('https://raw.githubusercontent.com/GettysburgDataScience/datasets/refs/heads/main/us_political/stats_america/Population-by-Age-and-Sex/Population%20by%20Age%20and%20Sex%20-%20US%2C%20States%2C%20Counties.csv')
race_df = pd.read_csv('https://raw.githubusercontent.com/GettysburgDataScience/datasets/refs/heads/main/us_political/stats_america/Population-by-Race/Population%20by%20Race%20-%20US%2C%20States%2C%20Counties.csv')
social_df = pd.read_csv('https://raw.githubusercontent.com/GettysburgDataScience/datasets/refs/heads/main/us_political/stats_america/Social-Context/Social%20Context.csv')
dev_df = pd.read_csv('https://raw.githubusercontent.com/GettysburgDataScience/datasets/refs/heads/main/us_political/stats_america/Metrics-For-Development/Metrics%20For%20Development.csv')


## Election Data

In [48]:
elec_df.head()

year    state state_po county_name  county_fips        office  \
0  2000  ALABAMA       AL     AUTAUGA       1001.0  US PRESIDENT   
1  2000  ALABAMA       AL     AUTAUGA       1001.0  US PRESIDENT   
2  2000  ALABAMA       AL     AUTAUGA       1001.0  US PRESIDENT   
3  2000  ALABAMA       AL     AUTAUGA       1001.0  US PRESIDENT   
4  2000  ALABAMA       AL     BALDWIN       1003.0  US PRESIDENT   

        candidate       party  candidatevotes  totalvotes   version   mode  
0         AL GORE    DEMOCRAT            4942       17208  20250821  TOTAL  
1  GEORGE W. BUSH  REPUBLICAN           11993       17208  20250821  TOTAL  
2           OTHER       OTHER             113       17208  20250821  TOTAL  
3     RALPH NADER       GREEN             160       17208  20250821  TOTAL  
4         AL GORE    DEMOCRAT           13997       56480  20250821  TOTAL

In [49]:
columns_to_keep = ['year', 'county_fips', 'candidate', 'candidatevotes', 'totalvotes']
elec_R_df = elec_df.query('party == "REPUBLICAN" and mode.str.startswith("TOTAL")')[columns_to_keep]
elec_D_df = elec_df.query('party == "DEMOCRAT" and mode.str.startswith("TOTAL")')[columns_to_keep]

In [50]:
elections_df = pd.merge(left = elec_D_df, right = elec_R_df,
         how = 'inner', on = ['year', 'county_fips'], suffixes = ['_D', '_R'])

elections_df.drop(columns = 'totalvotes_D', inplace = True)
elections_df.rename(columns = {'totalvotes_R':'totalvotes'})

elections_df.head()

year  county_fips candidate_D  candidatevotes_D     candidate_R  \
0  2000       1001.0     AL GORE              4942  GEORGE W. BUSH   
1  2000       1003.0     AL GORE             13997  GEORGE W. BUSH   
2  2000       1005.0     AL GORE              5188  GEORGE W. BUSH   
3  2000       1007.0     AL GORE              2710  GEORGE W. BUSH   
4  2000       1009.0     AL GORE              4977  GEORGE W. BUSH   

   candidatevotes_R  totalvotes_R  
0             11993         17208  
1             40872         56480  
2              5096         10395  
3              4273          7101  
4             12667         17973

In [51]:
fips_df = elec_df[['state_po', 'county_name', 'county_fips']].drop_duplicates().reset_index(drop = True)
fips_df.head()

state_po county_name  county_fips
0       AL     AUTAUGA       1001.0
1       AL     BALDWIN       1003.0
2       AL     BARBOUR       1005.0
3       AL        BIBB       1007.0
4       AL      BLOUNT       1009.0

In [52]:
## County Health Data

In [53]:
health_df.head(3)

State FIPS Code  County FIPS Code  5-digit FIPS Code State Abbreviation  \
0                0                 0                  0                 US   
1                1                 0               1000                 AL   
2                1                 1               1001                 AL   

             Name  Release Year  County Clustered (Yes=1/No=0)  \
0   United States          2025                            NaN   
1         Alabama          2025                            NaN   
2  Autauga County          2025                            1.0   

   Premature Death raw value  Premature Death numerator  \
0                8351.736549                  4763989.0   
1               11853.247248                   102760.0   
2                9938.263382                     1008.0   

   Premature Death denominator  ...  % Rural raw value  % Rural numerator  \
0                  925367214.0  ...           0.200031         66300254.0   
1                   13958454.0  ...           0.422628          2123399.0   
2                     163064.0  ...           0.406768            23920.0   

   % Rural denominator  % Rural CI low  % Rural CI high  Population raw value  \
0          331449281.0             NaN              NaN           334914895.0   
1            5024279.0             NaN              NaN             5108468.0   
2              58805.0             NaN              NaN               60342.0   

   Population numerator  Population denominator  Population CI low  \
0                   NaN                     NaN                NaN   
1                   NaN                     NaN                NaN   
2                   NaN                     NaN                NaN   

   Population CI high  
0                 NaN  
1                 NaN  
2                 NaN  

[3 rows x 796 columns]

In [54]:
def print_cols(df, num_cols = 2):
    col_str = ''
    for k, col in enumerate(df.columns):
        col_str += f'{k:>3}.  {col:<40}'
        if k % num_cols == 0:
            col_str += '\n'
    print(col_str)
    
print_cols(health_df, num_cols = 4)

  0.  State FIPS Code                         
  1.  County FIPS Code                          2.  5-digit FIPS Code                         3.  State Abbreviation                        4.  Name                                    
  5.  Release Year                              6.  County Clustered (Yes=1/No=0)             7.  Premature Death raw value                 8.  Premature Death numerator               
  9.  Premature Death denominator              10.  Premature Death CI low                   11.  Premature Death CI high                  12.  Premature Death flag (0 = No Flag/1=Unreliable/2=Suppressed)
 13.  Premature Death (AIAN)                   14.  Premature Death CI low (AIAN)            15.  Premature Death CI high (AIAN)           16.  Premature Death flag (AIAN) (. = No Flag/1=Unreliable/2=Suppressed)
 17.  Premature Death (Asian)                  18.  Premature Death CI low (Asian)           19.  Premature Death CI high (Asian)          20.  Premature Death flag (

## County Age-Sex Data

## County Age-Sex Data

In [55]:
agesex_df.iloc[40:60]

IBRC_Geo_ID  Statefips  Countyfips         Description  Year  \
40         1000          1           0             Alabama  2015   
41         1000          1           0             Alabama  2016   
42         1000          1           0             Alabama  2017   
43         1000          1           0             Alabama  2018   
44         1000          1           0             Alabama  2019   
45         1000          1           0             Alabama  2020   
46         1000          1           0             Alabama  2021   
47         1000          1           0             Alabama  2022   
48         1000          1           0             Alabama  2023   
49         1000          1           0             Alabama  2024   
50         1001          1           1  Autauga County, AL  2000   
51         1001          1           1  Autauga County, AL  2001   
52         1001          1           1  Autauga County, AL  2002   
53         1001          1           1  Autauga County, AL  2003   
54         1001          1           1  Autauga County, AL  2004   
55         1001          1           1  Autauga County, AL  2005   
56         1001          1           1  Autauga County, AL  2006   
57         1001          1           1  Autauga County, AL  2007   
58         1001          1           1  Autauga County, AL  2008   
59         1001          1           1  Autauga County, AL  2009   

    Total Population  Population 0-4  Population 5-17  Population 18-24  \
40           4854803          294097           809062            471910   
41           4866824          294616           805845            462098   
42           4877989          294572           802005            455547   
43           4891628          295520           797079            453230   
44           4907965          294274           794453            450764   
45           5033094          297347           832329            467246   
46           5049196          294227           833920            475424   
47           5076181          293480           836216            478391   
48           5117673          294447           839471            482743   
49           5157699          295446           839411            488175   
50             44021            3029             9538              3520   
51             44889            3120             9574              3654   
52             45909            3191             9864              3661   
53             46800            3192            10110              3768   
54             48366            3353            10389              4015   
55             49676            3487            10662              4100   
56             51328            3492            10947              4255   
57             52405            3485            11264              4290   
58             53277            3437            11411              4427   
59             54135            3584            11312              4545   

    Population 25-44  Population 45-64  Population 65+  Population Under 18  \
40           1230689           1286744          762301              1103159   
41           1231213           1289047          784005              1100461   
42           1233167           1287432          805266              1096577   
43           1236516           1282303          826980              1092599   
44           1242294           1274660          851520              1088727   
45           1270670           1299444          866058              1129676   
46           1277137           1287898          880590              1128147   
47           1285214           1279704          903176              1129696   
48           1296732           1274413          929867              1133918   
49           1309411           1269355          955901              1134857   
50             13444              9959            4531                12567   
51             13507             10367            4

## County Race Data

In [56]:
race_df.head()

IBRC_Geo_ID  Statefips  Countyfips Description  Year  Total Population  \
0            0          0           0        U.S.  1990         249622814   
1            0          0           0        U.S.  1991         252980941   
2            0          0           0        U.S.  1992         256514224   
3            0          0           0        U.S.  1993         259918588   
4            0          0           0        U.S.  1994         263125821   

   White Alone  Black Alone  American Indian or Alaskan Native  Asian Alone  \
0  209366661.0   30648345.0                          2058726.0    7549082.0   
1  211606011.0   31290743.0                          2126968.0    7957219.0   
2  213945622.0   31979982.0                          2202176.0    8386444.0   
3  216187073.0   32634735.0                          2282052.0    8814728.0   
4  218304774.0   33258981.0                          2361078.0    9200988.0   

   Hawaiian or Pacific Islander Alone  Two or More Races  Not Hispanic  \
0                                 NaN                NaN   227049976.0   
1                                 NaN                NaN   229425951.0   
2                                 NaN                NaN   231894879.0   
3                                 NaN                NaN   234141927.0   
4                                 NaN                NaN   236179888.0   

     Hispanic  
0  22572838.0  
1  23554990.0  
2  24619345.0  
3  25776661.0  
4  26945933.0

## County Social Leanings Data

In [57]:
social_df.head()

IBRC_Geo_ID  Statefips  Countyfips      Description  Year  \
0        10001         10           1  Kent County, DE  2019   
1        10001         10           1  Kent County, DE  2019   
2        10001         10           1  Kent County, DE  2019   
3        10001         10           1  Kent County, DE  2019   
4        10001         10           1  Kent County, DE  2019   

   Social_Context_Code Social_Context_Code_Description  \
0                  211                     Hopefulness   
1                  104                 Employment Rate   
2                  103               Income Per Capita   
3                  102                 Income Mobility   
4                  101                Entrepreneurship   

   Social_Context_Domain_Data Time_Period  
0                   87.332678   1972-2017  
1                   95.300000        2017  
2                26118.000000        2017  
3                   -0.441463        2017  
4                   10.732984        2013

In [58]:
social_df.pivot(index = ['IBRC_Geo_ID', 'Time_Period'], columns = 'Social_Context_Code_Description', values = 'Social_Context_Domain_Data')

Social_Context_Code_Description  Agreeableness  Belief In Science  \
IBRC_Geo_ID Time_Period                                             
1001        1972-2017                      NaN          70.833333   
            1999-2017                86.279655                NaN   
            2013                           NaN                NaN   
            2017                           NaN                NaN   
1003        1972-2017                      NaN          63.268161   
...                                        ...                ...   
56043       2017                           NaN                NaN   
56045       1972-2017                      NaN          67.710969   
            1999-2017                88.251855                NaN   
            2013                           NaN                NaN   
            2017                           NaN                NaN   

Social_Context_Code_Description  Collectivism  Conflict Awareness  \
IBRC_Geo_ID Time_Period                                             
1001        1972-2017               57.142857           63.444323   
            1999-2017                     NaN                 NaN   
            2013                          NaN                 NaN   
            2017                          NaN                 NaN   
1003        1972-2017               67.948815           63.751017   
...                                       ...                 ...   
56043       2017                          NaN                 NaN   
56045       1972-2017               69.084172           56.654563   
            1999-2017                     NaN                 NaN   
            2013                          NaN                 NaN   
            2017                          NaN                 NaN   

Social_Context_Code_Description  Conscientiousness    Empathy  \
IBRC_Geo_ID Time_Period                                         
1001        1972-2017                          NaN  83.308726   
            1999-2017                    84.113820        NaN   
            2013                               NaN        NaN   
            2017                               NaN        NaN   
1003        1972-2017                          NaN  78.187835   
...                                            ...        ...   
56043       2017                               NaN        NaN   
56045       1972-2017                          NaN  81.012828   
            1999-2017                    84.263823        NaN   
            2013                               NaN        NaN   
            2017                               NaN        NaN   

Social_Context_Code_Description  Employment Rate  Entrepreneurship  \
IBRC_Geo_ID Time_Period                                              
1001        1972-2017                        NaN               NaN   
            1999-2017                        NaN               NaN   
            2013                             NaN         12.968300   
            2017                            94.7               NaN   
1003        1972-2017                        NaN               NaN   
...                                          ...               ...   
56043       2017                            95.3               NaN   
56045       1972-2017                        NaN               NaN   
            1999-2017                        NaN               NaN   
            2013                             NaN          7.446809   
            2017                            95.1               NaN   

Social_Context_Code_Description  Extraversion  Gender Equality  Hopefulness  \
IBRC_Geo_ID Time_Period                                                       
1001        1972-2017                     NaN        77.063492    91.163142   
            1999-2017               86.112526              NaN          NaN   
            2013                          NaN              NaN          NaN   
            2017                          NaN       

## County Development Metrics Data

In [59]:
dev_df.head()

IBRC_Geo_ID  Statefips  Countyfips         Description  Year  M4D_Code  \
0         1001          1           1  Autauga County, AL  2019       100   
1         1001          1           1  Autauga County, AL  2019      1000   
2         1001          1           1  Autauga County, AL  2019     10000   
3         1001          1           1  Autauga County, AL  2019     10100   
4         1001          1           1  Autauga County, AL  2019     10200   

              Code Description   M4D_Data  
0           Headline M4D Index   0.666112  
1               Full-Time Work   0.661573  
2    Grocery stores per capita   0.072548  
3  Farmers' markets per capita   0.018166  
4     SNAP benefits per capita  17.905272

In [60]:
# dev_df.drop_duplicates(inplace=True)
# dev_df.pivot(index = ['IBRC_Geo_ID', 'Year'], columns = 'Code Description', values = 'M4D_Data')

## County Age-Sex Data